In [1]:
import pandas as pd
import numpy as np
import plotly
from pathlib import Path
import plotly.express as px
import plotly.graph_objects as go
from tqdm.auto import tqdm

from sklearn.metrics import f1_score
from sklearn.model_selection import KFold
from lightgbm import LGBMClassifier
import joblib
import hrvanalysis

In [2]:
df = pd.read_csv(Path('../data/train.csv'))

In [3]:
df = df.sort_values(['id', 'time'])

In [4]:
hrv_df = df.copy()

In [5]:
samples = df['id'].unique()
WINDOW_SIZE = 25
HALF_WINDOW = int((WINDOW_SIZE-1)/2)
QART_WINDOW = int((WINDOW_SIZE-1)/4)
LOW_BOUND = 380
UPPER_BOUND = 1400

In [6]:
samples = hrv_df['id'].unique()

In [7]:
intervals = []
for s in tqdm(samples):
    rr = hrv_df[hrv_df.id == s]['x'].values
    rr = hrvanalysis.preprocessing.remove_outliers(rr, low_rri=LOW_BOUND, high_rri=UPPER_BOUND)
    rr = hrvanalysis.preprocessing.interpolate_nan_values(rr)
    intervals.extend(rr)

  0%|          | 0/229 [00:00<?, ?it/s]

44 outlier(s) have been deleted.
The outlier(s) value(s) are : [316, 340, 352, 228, 204, 324, 180, 1444, 348, 368, 256, 364, 1732, 128, 344, 340, 236, 1688, 1632, 116, 248, 136, 1844, 364, 1584, 316, 200, 200, 1520, 1592, 1532, 1604, 1692, 364, 376, 212, 316, 120, 196, 152, 20, 332, 372, 72]
1 outlier(s) have been deleted.
The outlier(s) value(s) are : [132]
0 outlier(s) have been deleted.
0 outlier(s) have been deleted.
0 outlier(s) have been deleted.
0 outlier(s) have been deleted.
0 outlier(s) have been deleted.
24 outlier(s) have been deleted.
The outlier(s) value(s) are : [328, 280, 104, 292, 312, 264, 340, 224, 208, 2436, 160, 220, 244, 160, 236, 2924, 316, 304, 208, 128, 256, 356, 280, 340]
29 outlier(s) have been deleted.
The outlier(s) value(s) are : [280, 360, 376, 304, 112, 148, 232, 344, 284, 112, 1552, 324, 160, 276, 348, 252, 216, 316, 316, 208, 112, 340, 296, 272, 356, 252, 232, 344, 328]
52 outlier(s) have been deleted.
The outlier(s) value(s) are : [160, 288, 332, 212,

21 outlier(s) have been deleted.
The outlier(s) value(s) are : [1420, 240, 80, 44, 1440, 1440, 140, 360, 340, 20, 340, 360, 220, 220, 40, 360, 260, 280, 144, 300, 1420]
15 outlier(s) have been deleted.
The outlier(s) value(s) are : [260, 360, 320, 280, 260, 364, 320, 360, 1440, 200, 240, 180, 220, 320, 1440]
1 outlier(s) have been deleted.
The outlier(s) value(s) are : [1420]
45 outlier(s) have been deleted.
The outlier(s) value(s) are : [240, 200, 180, 100, 300, 100, 220, 284, 220, 240, 180, 240, 1464, 80, 320, 320, 180, 280, 184, 220, 280, 236, 100, 360, 60, 360, 280, 264, 240, 140, 280, 220, 200, 320, 320, 220, 200, 360, 160, 160, 260, 160, 300, 120, 340]
24 outlier(s) have been deleted.
The outlier(s) value(s) are : [2264, 1700, 128, 276, 352, 140, 288, 284, 288, 288, 1720, 320, 248, 360, 360, 108, 300, 292, 172, 240, 344, 216, 360, 1792]
0 outlier(s) have been deleted.
3 outlier(s) have been deleted.
The outlier(s) value(s) are : [1792, 348, 248]
75 outlier(s) have been deleted.
T

279 outlier(s) have been deleted.
The outlier(s) value(s) are : [300, 180, 204, 220, 356, 44, 340, 200, 372, 176, 284, 204, 304, 328, 72, 204, 376, 288, 344, 244, 200, 1676, 268, 248, 324, 264, 296, 148, 368, 48, 176, 312, 120, 320, 1828, 328, 284, 32, 4100, 88, 332, 248, 136, 300, 268, 316, 184, 232, 224, 312, 144, 68, 244, 192, 112, 240, 188, 276, 212, 48, 116, 260, 320, 368, 136, 376, 152, 276, 312, 212, 228, 220, 280, 168, 104, 188, 276, 312, 348, 100, 288, 48, 296, 204, 168, 368, 164, 272, 184, 240, 212, 360, 80, 232, 100, 140, 244, 288, 200, 316, 216, 28, 136, 164, 112, 376, 272, 260, 164, 228, 196, 104, 268, 28, 296, 232, 232, 144, 352, 300, 200, 308, 152, 140, 240, 312, 364, 24, 328, 228, 316, 148, 200, 244, 368, 232, 320, 76, 300, 364, 284, 48, 48, 84, 244, 36, 260, 248, 328, 148, 284, 156, 340, 316, 236, 232, 104, 308, 76, 176, 292, 164, 296, 180, 300, 232, 228, 344, 240, 188, 208, 368, 104, 268, 200, 348, 352, 212, 36, 316, 160, 316, 272, 252, 220, 2776, 248, 264, 1448, 3664

In [8]:
hrv_df['x'] = intervals

In [9]:
def pop_arr(arr, num):
    s = len(arr)
    return np.resize(np.repeat(np.resize(arr[:s], (1,s)), num, axis=0), (num*s,))

In [10]:
def timedomain(rr, mask):
    results = {}
    
    rr = rr[mask==1]
    
    if len(rr) > 1:
        hr = 60000/rr
    
        results['mean_RR'] = np.mean(rr)
        results['std_rr_sdnn'] = np.std(rr)
        results['mean_hr_kubious'] = 60000/np.mean(rr)
        results['mean_hr'] = np.mean(hr)
        results['std_hr'] = np.std(hr)
        results['min_hr'] = np.min(hr)
        results['max_hr'] = np.max(hr)
        results['rmssd'] = np.sqrt(np.mean(np.square(np.diff(rr))))
        results['nn_xx'] = np.sum(np.abs(np.diff(rr)) > 50)*1
        results['pnn_xx'] = 100 * np.sum((np.abs(np.diff(rr)) > 50)*1) / len(rr)
    else:
        results['mean_RR'] = 0
        results['std_rr_sdnn'] = 0
        results['mean_hr_kubious'] = 0
        results['mean_hr'] = 0
        results['std_hr'] = 0
        results['min_hr'] = 0
        results['max_hr'] = 0
        results['rmssd'] = 0
        results['nn_xx'] = 0
        results['pnn_xx'] = 0

    return results

In [12]:
new_hrv_df = []
for sample in tqdm(samples):
    # get array
    loc_df = hrv_df[hrv_df.id==sample].sort_values('time').reset_index(drop=True)
    arr = loc_df['x'].values
    
    time = loc_df['time'].values

    # ext array with 8 points to each direction
    
    arr = np.concatenate((
        pop_arr(arr[:2], QART_WINDOW),
        arr,
        pop_arr(arr[-2:], QART_WINDOW),
    ))

    for i in range(HALF_WINDOW+1, len(arr)-HALF_WINDOW+1):
        local_window = arr[i-HALF_WINDOW-1:i+HALF_WINDOW+2]
        nn = hrvanalysis.preprocessing.get_nn_intervals(local_window)
        nn = [v for v in nn if not np.isnan(v)]
        try:
            domain_features = hrvanalysis.extract_features.get_time_domain_features(nn)
        except:
            domain_features = {}
        try:
            frequency_domain_features = hrvanalysis.extract_features.get_frequency_domain_features(nn)
        except:
            frequency_domain_features = {}
        try:
            geometrical_feature = hrvanalysis.extract_features.get_geometrical_features(nn)
        except:
            geometrical_feature = {}
        try:
            poincare_plot_features = hrvanalysis.extract_features.get_poincare_plot_features(nn)
        except:
            poincare_plot_features = {}
        try:
            csi_cvi_features = hrvanalysis.extract_features.get_csi_cvi_features(nn)
        except:
            csi_cvi_features = {}
        try:
            sampen = hrvanalysis.extract_features.get_sampen(nn)
        except:
            sampen = {}
        
        new_hrv_df.append({'id': sample, 
                       'time': time[i-HALF_WINDOW-1],
                        **{f"hrv_x_{x}":y for x,y in zip(range(-8,9), local_window)},
                        **{f"hrv_nn {x}":y for x,y in enumerate(nn)},
                        **domain_features,
                        **frequency_domain_features,
                        **geometrical_feature,
                        **poincare_plot_features,
                        **csi_cvi_features,
                        **sampen,
                      })

  0%|          | 0/229 [00:00<?, ?it/s]

0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have

c:\users\glebe\anaconda3\envs\cardiospike--8ortirp-py3.8\lib\site-packages\scipy\signal\spectral.py:1961: UserWarning: nperseg = 256 is greater than input length  = 85, using nperseg = 85
  warnings.warn('nperseg = {0:d} is greater than input length '
c:\users\glebe\anaconda3\envs\cardiospike--8ortirp-py3.8\lib\site-packages\scipy\signal\spectral.py:1961: UserWarning: nperseg = 256 is greater than input length  = 86, using nperseg = 86
  warnings.warn('nperseg = {0:d} is greater than input length '
c:\users\glebe\anaconda3\envs\cardiospike--8ortirp-py3.8\lib\site-packages\scipy\signal\spectral.py:1961: UserWarning: nperseg = 256 is greater than input length  = 84, using nperseg = 84
  warnings.warn('nperseg = {0:d} is greater than input length '
c:\users\glebe\anaconda3\envs\cardiospike--8ortirp-py3.8\lib\site-packages\scipy\signal\spectral.py:1961: UserWarning: nperseg = 256 is greater than input length  = 83, using nperseg = 83
  warnings.warn('nperseg = {0:d} is greater than input l

0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have

c:\users\glebe\anaconda3\envs\cardiospike--8ortirp-py3.8\lib\site-packages\scipy\signal\spectral.py:1961: UserWarning: nperseg = 256 is greater than input length  = 76, using nperseg = 76
  warnings.warn('nperseg = {0:d} is greater than input length '
c:\users\glebe\anaconda3\envs\cardiospike--8ortirp-py3.8\lib\site-packages\scipy\signal\spectral.py:1961: UserWarning: nperseg = 256 is greater than input length  = 75, using nperseg = 75
  warnings.warn('nperseg = {0:d} is greater than input length '
c:\users\glebe\anaconda3\envs\cardiospike--8ortirp-py3.8\lib\site-packages\scipy\signal\spectral.py:1961: UserWarning: nperseg = 256 is greater than input length  = 74, using nperseg = 74
  warnings.warn('nperseg = {0:d} is greater than input length '
c:\users\glebe\anaconda3\envs\cardiospike--8ortirp-py3.8\lib\site-packages\scipy\signal\spectral.py:1961: UserWarning: nperseg = 256 is greater than input length  = 73, using nperseg = 73
  warnings.warn('nperseg = {0:d} is greater than input l

...


2 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
2 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
2 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
2 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
2 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
2 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
1 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
1 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
1 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
1 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
1 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
1 ectopic beat(s) have been deleted with kamath rule.

c:\users\glebe\anaconda3\envs\cardiospike--8ortirp-py3.8\lib\site-packages\scipy\signal\spectral.py:1961: UserWarning: nperseg = 256 is greater than input length  = 60, using nperseg = 60
  warnings.warn('nperseg = {0:d} is greater than input length '



0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
0 ectopic beat(s) have been deleted with kamath rule.

c:\users\glebe\anaconda3\envs\cardiospike--8ortirp-py3.8\lib\site-packages\scipy\signal\spectral.py:1961: UserWarning: nperseg = 256 is greater than input length  = 59, using nperseg = 59
  warnings.warn('nperseg = {0:d} is greater than input length '
c:\users\glebe\anaconda3\envs\cardiospike--8ortirp-py3.8\lib\site-packages\scipy\signal\spectral.py:1961: UserWarning: nperseg = 256 is greater than input length  = 58, using nperseg = 58
  warnings.warn('nperseg = {0:d} is greater than input length '
c:\users\glebe\anaconda3\envs\cardiospike--8ortirp-py3.8\lib\site-packages\scipy\signal\spectral.py:1961: UserWarning: nperseg = 256 is greater than input length  = 56, using nperseg = 56
  warnings.warn('nperseg = {0:d} is greater than input length '
c:\users\glebe\anaconda3\envs\cardiospike--8ortirp-py3.8\lib\site-packages\scipy\signal\spectral.py:1961: UserWarning: nperseg = 256 is greater than input length  = 54, using nperseg = 54
  warnings.warn('nperseg = {0:d} is greater than input l

0 outlier(s) have been deleted.
2 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
2 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
2 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
2 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
2 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
2 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
1 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
1 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
1 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
1 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
1 ectopic beat(s) have been deleted with kamath rule.
0 outlier(s) have been deleted.
1 ectopic beat(s) have

In [15]:
new_hrv_df = pd.DataFrame(new_hrv_df)

In [17]:
new_hrv_df.fillna(0, inplace=True)

In [24]:
new_df = []
for sample in tqdm(samples):
    # get array
    loc_df = df[df.id==sample].sort_values('time').reset_index(drop=True)
    arr = loc_df['x'].values
    
    target = loc_df['y'].values
    
    time = loc_df['time'].values
    
    mask = ((arr>LOW_BOUND) & (arr < UPPER_BOUND)).astype(int)
    # ext array with 8 points to each direction
    
    arr = np.concatenate((
        pop_arr(arr[:2], QART_WINDOW),
        arr,
        pop_arr(arr[-2:], QART_WINDOW),
    ))
    
    mask = np.concatenate((
        pop_arr([0], HALF_WINDOW),
        mask,
        pop_arr([0], HALF_WINDOW)
    ))
    for i in range(HALF_WINDOW+1, len(arr)-HALF_WINDOW+1):
        local_window = arr[i-HALF_WINDOW-1:i+HALF_WINDOW+2]
        local_mask = mask[i-HALF_WINDOW-1:i+HALF_WINDOW+2]
        new_df.append({'id': sample, 
                       'time': time[i-HALF_WINDOW-1],
                       **{f"x_{x}":y for x,y in zip(range(-8,9), local_window)},
                      'target': target[i-HALF_WINDOW-1],
                       **{f"mask_{x}":y for x,y in zip(range(-8,9), local_mask)},
                       **timedomain(local_window, local_mask),
                       **{f"delta_{x}":y for x,y in zip(range(WINDOW_SIZE-1), np.diff(local_window))},
                      })

  0%|          | 0/229 [00:00<?, ?it/s]

In [25]:
new_df=pd.DataFrame(new_df)

In [26]:
new_df.shape

(60487, 71)

In [27]:
new_hrv_df.shape

(60487, 78)

In [28]:
new_hrv_df.head()

id  time  hrv_x_-8  hrv_x_-7  hrv_x_-6  hrv_x_-5  hrv_x_-4  hrv_x_-3  \
0   1     0     800.0     780.0     800.0     780.0     800.0     780.0   
1   1   780     780.0     800.0     780.0     800.0     780.0     800.0   
2   1  1572     800.0     780.0     800.0     780.0     800.0     780.0   
3   1  2392     780.0     800.0     780.0     800.0     780.0     800.0   
4   1  3196     800.0     780.0     800.0     780.0     800.0     780.0   

   hrv_x_-2  hrv_x_-1  ...         vlf  triangular_index  tinn        sd1  \
0     800.0     780.0  ...  369.862002          3.857143     0  24.338384   
1     780.0     800.0  ...  513.848649          3.857143     0  24.228908   
2     800.0     780.0  ...  722.445449          4.500000     0  24.502433   
3     780.0     800.0  ...  904.533296          4.500000     0  25.137162   
4     800.0     780.0  ...  969.055602          5.400000     0  25.715126   

         sd2  ratio_sd2_sd1       csi       cvi  Modified_csi    sampen  
0  80.365878       3.302022  3.302022  4.495483   1061.479593  0.308301  
1  83.561686       3.448842  3.448842  4.510461   1152.764349  0.360003  
2  84.199573       3.436376  3.436376  4.518639   1157.365564  0.418710  
3  83.987301       3.341161  3.341161  4.528650   1122.460302  0.470004  
4  84.052199       3.268590  3.268590  4.538858   1098.928664  0.523248  

[5 rows x 78 columns]

In [30]:
new_df=new_df.merge(new_hrv_df, on=['id', 'time'])

In [31]:
from sklearn.metrics import roc_curve, precision_recall_curve, f1_score

def threshold_search(y_true, y_proba):
    precision , recall, thresholds = precision_recall_curve(y_true, y_proba)
    thresholds = np.append(thresholds, 1.001) 
    F = 2 / (1 / (precision + 1e-18) + 1 / (recall + 1e-18))
    F[F>1.0] = 0
    best_score = np.max(F)
    best_th = thresholds[np.argmax(F)]
    return best_th , best_score

In [39]:
lgbm_params = {
    'num_leaves': 52,
    'learning_rate': 0.028067101239171117,
    'class_weight': None,
    'min_split_gain': 0.2079596284724723,
    'min_child_samples': 26,
    'subsample': 0.9964018869175387,
    'subsample_freq': 3,
    'colsample_bytree': 0.7621469158134937,
    'reg_alpha': 0.0007822636610799144,
    'reg_lambda': 4.076057666254058,
    'boosting_type': 'gbdt',  
    'objective': 'binary',  
    'n_estimators': 3000, 
    'random_state': 13
}

In [40]:
drop_cols = ['id', 'time', 'target']
traget_col = 'target'

In [41]:
kf = KFold(n_splits=5, shuffle=True, random_state=42)
inner_kf = KFold(n_splits=5, shuffle=True, random_state=239)

df_ids = df['id'].unique()
folds_data = []

predicts = dict()

for outer_fold, (train_id, val_id) in enumerate(kf.split(df_ids)):

    outer_train_samples = df_ids[train_id]
    outer_val_samples = df_ids[val_id]
    
    outer_train_df = new_df[new_df.id.isin(outer_train_samples)]
    outer_val_df = new_df[new_df.id.isin(outer_val_samples)]
    
    predicts[outer_fold] = []
    
    for inner_fold, (inner_train_id, inner_val_id) in enumerate(inner_kf.split(outer_train_samples)):
        model = LGBMClassifier(**lgbm_params)
        inner_train_samples = outer_train_samples[inner_train_id]
        inner_val_samples = outer_train_samples[inner_val_id]
        
        inner_train_df = new_df[new_df.id.isin(inner_train_samples)]
        inner_val_df = new_df[new_df.id.isin(inner_val_samples)].reset_index(drop=True)
    
        model.fit(inner_train_df.drop(columns=drop_cols), inner_train_df[traget_col],
                  eval_set = (outer_val_df.drop(columns=drop_cols),
                              outer_val_df[traget_col]),
                  early_stopping_rounds=150,
                  eval_metric='logloss',
                  verbose=False)
        
        joblib.dump(model, f"1_lgbm_model_o{outer_fold}_i{inner_fold}.joblib")
        
        valid_y_true = outer_val_df[traget_col].values
        valid_y_proba = model.predict_proba(outer_val_df.drop(columns=drop_cols))[:,1]
        best_th , best_score = threshold_search(valid_y_true, valid_y_proba)
                     

        inner_test_y_true = inner_val_df[traget_col].values.astype(int)
        inner_test_y_predict = model.predict_proba(inner_val_df.drop(columns=drop_cols))[:,1]
        inner_val_df['predict'] = inner_test_y_predict
        
        predicts[outer_fold].append(inner_val_df[['id', 'time', 'predict']])
        
        score = f1_score(inner_test_y_true, (inner_test_y_predict > best_th).astype(int))
        
        fold_data = {"outer_fold": outer_fold, 
                     "inner_fold": inner_fold, 
                     "th": best_th, 
                     "test_f1": score, 
                     "val_f1": best_score}
        folds_data.append(fold_data)
        print(fold_data)


{'outer_fold': 0, 'inner_fold': 0, 'th': 0.361759076710607, 'test_f1': 0.8455284552845529, 'val_f1': 0.8225419664268584}
{'outer_fold': 0, 'inner_fold': 1, 'th': 0.3637465318536095, 'test_f1': 0.8642226748133062, 'val_f1': 0.8337777777777777}
{'outer_fold': 0, 'inner_fold': 2, 'th': 0.37323520061139315, 'test_f1': 0.7093348239239798, 'val_f1': 0.8347671314150102}
{'outer_fold': 0, 'inner_fold': 3, 'th': 0.284868449150459, 'test_f1': 0.8755570791909495, 'val_f1': 0.8213767063607319}
{'outer_fold': 0, 'inner_fold': 4, 'th': 0.3243575680201625, 'test_f1': 0.8770764119601329, 'val_f1': 0.8218289085545722}
{'outer_fold': 1, 'inner_fold': 0, 'th': 0.41463507703649044, 'test_f1': 0.863458110516934, 'val_f1': 0.7421652421652422}
{'outer_fold': 1, 'inner_fold': 1, 'th': 0.43061770272130656, 'test_f1': 0.84620886981402, 'val_f1': 0.737381126554499}
{'outer_fold': 1, 'inner_fold': 2, 'th': 0.46745466493274046, 'test_f1': 0.8253725640045854, 'val_f1': 0.7300884955752213}
{'outer_fold': 1, 'inner_f

In [42]:
results = pd.DataFrame(folds_data)

In [43]:
results.test_f1.mean()

0.829967560650336

In [44]:
results.val_f1.mean()

0.8342968095131842

In [45]:
results.th.mean()

0.337678524003066

In [67]:
df_feat = df[['id', 'time']].copy()

In [68]:
for i,v in predicts.items():
    part_df = pd.concat(v)
    part_df.columns = ['id', 'time', i]
    df_feat = df_feat.merge(part_df, how='left', left_on=['id', 'time'], right_on=['id', 'time'])

In [69]:
df_feat

id    time         0         1         2         3         4
0        1       0  0.014039  0.057720       NaN  0.029558  0.010225
1        1     780  0.022028  0.059655       NaN  0.030751  0.004688
2        1    1572  0.013267  0.057079       NaN  0.024134  0.007385
3        1    2392  0.019658  0.071962       NaN  0.043476  0.021869
4        1    3196  0.022806  0.067860       NaN  0.038839  0.010556
...    ...     ...       ...       ...       ...       ...       ...
60482  275  115360  0.974030  0.884394  0.984954  0.971759       NaN
60483  275  115912  0.952401  0.811262  0.970726  0.958469       NaN
60484  275  116464  0.653215  0.655431  0.714523  0.718442       NaN
60485  275  117020  0.180580  0.257770  0.156364  0.164410       NaN
60486  275  117572  0.022131  0.053656  0.036663  0.017426       NaN

[60487 rows x 7 columns]

In [70]:
df_feat['mean'] = df_feat[[0, 1, 2, 3, 4]].mean(axis=1)

In [71]:
joblib.dump(df_feat[['id', 'time', 'mean']], 'feat1.joblib')

['feat1.joblib']

In [72]:
from scipy.stats import gmean

In [79]:
def nan_gmean(x):
    return gmean(x[~np.isnan(x)])

In [76]:
arr = df_feat[[0, 1, 2, 3, 4]].loc[0]

In [80]:
df_feat['gmean'] = df_feat[[0, 1, 2, 3, 4]].apply(nan_gmean, axis=1)

In [82]:
joblib.dump(df_feat[['id', 'time', 'gmean']], 'feat1_gmean.joblib')

['feat1_gmean.joblib']